In [1]:
# load modules
import pandas as pd
import altair as alt
import numpy as np

In [73]:
data = pd.read_pickle('C:/Users/614532416/python_scripts/3. Processed Data/bh_proc_data.pkl')
grp_df = pd.read_pickle('C:/Users/614532416/python_scripts/3. Processed Data/bh_grp_non_res_data.pkl')
site_1141 = pd.read_pickle('C:/Users/614532416/python_scripts/3. Processed Data/site_1141.pkl')

In [82]:
site_1141.rename(columns={"SNE ID": "DND", "1141 Code": "Location"}, inplace=True)

In [85]:
site_1141.head(2)

Location Location Chassis Category Device Model date
0    L/SWS  5712725       Upgradable   7750 SR-12  NaN
1      AAI  5468836        Strategic   7750 SR-a4  NaN

In [39]:
# required to work with more than 10,000 points in altair
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [65]:
data.head(2)

SNE  Max Rx Tx       date  Failover Capacity  Total Capacity  \
0  3328444   0.505002 2023-11-05                2.0             4.0   
1  3328444   0.473073 2023-10-29                2.0             4.0   

   trend_val 1141 Code  
0   0.521603       LTK  
1   0.521998       LTK

In [80]:
data.rename(columns={"SNE": "DND", "1141 Code": "Location"}, inplace=True)

In [81]:
grp_df.rename(columns={"SNE": "DND", "1141 Code": "Location"}, inplace=True)

In [86]:
# create altair search boxes and bind to selection_points

genre_dropdown = alt.binding(input = 'search', name="SNEID ") # input = 'search', input = ['select'], binding_select(options=genres,
genre_select = alt.selection_point(fields=['DND'], bind=genre_dropdown, value = '21020500')

site_dropdown = alt.binding(input = 'search', name=" ")
site_select = alt.selection_point(fields=['Location'], bind=site_dropdown, value = 'ACW')
s_select = alt.selection_point(fields=['SNE ID'], empty = False) # to select color on table for 1141 code filtering

In [95]:
# base chart showing traffic trend
base = alt.Chart(data).encode(alt.X('date',  axis=alt.Axis(format="%b %y", labelSeparation = 30)).title(''), 
tooltip = ['DND', 'Max Rx Tx', 'trend_val', 'date', 'Location'])
Chart = alt.layer(
    base.mark_point(color='blue', size = 30, opacity = 0.2).encode(y='Max Rx Tx'),
    base.mark_line(color='blue', strokeWidth=1.5).encode(alt.Y('Max Rx Tx').title('Traffic (TBps)')), 
    base.mark_line(color='orange', strokeWidth=1).encode(y='trend_val'),
    base.mark_point(color='blue', size = 60, opacity = 0).encode(y='trend_val'),
    base.mark_line(color='#2ca02c', strokeWidth=1.25, strokeDash=[3,2]).encode(y='Failover Capacity'),
    base.mark_line(color='#2ca02c', strokeWidth=1.25, strokeDash=[3,2]).encode(y='Total Capacity')
).properties(
    width=750)

In [103]:
from IPython.display import HTML
display(HTML("""
<style>
.vega-bind {
  text-align:center;
  position: absolute;
  font-weight: bold;
  top: 380px;
  left: 985px;
}
.vega-bind ~ .vega-bind{
  text-align:center;
  position: absolute;
  font-weight: bold;
  top: 345px;
  left: 554.8px;
}
.vega-bind input[type=search]  {
  background: #f1f1f1;
  border: 1px solid grey;
  padding: 4px;
}
</style>
"""))
# Brush for selection
brush = alt.selection_point(fields=['date'])#, value = '3')
click = alt.selection_point(fields=['DND'], value = '21020500')
d_select = alt.selection_point(fields=['DND'],  empty=False, value = '5399517')


# Scatter Plot
points = alt.Chart(grp_df.sort_values('date')).mark_bar().encode(
    x= alt.X('date', axis=alt.Axis(labelAngle=-45, labelOverlap = True, labelSeparation = 3)).title(''),
    y= alt.Y('count(DND):Q'),
    color= alt.Color('status').scale(scheme = 'spectral', reverse=False), 
    opacity=alt.condition(brush, alt.OpacityValue(1), alt.OpacityValue(0.6)),
    tooltip = ['status', 'date']
).add_params(brush)#.transform_filter(d_select)

# Base chart for data tables
ranked_text = alt.Chart(grp_df).mark_text(align='right', fontSize = 13).encode(
    y=alt.Y('row_number:O').axis(None),
    #size=alt.condition(d_select, alt.value(14), alt.value(13)),
    #fontWeight=alt.condition(d_select, alt.value(14), alt.value(13)),
    color=alt.condition(d_select, alt.value('#0a326a'), alt.value('black'))
).transform_filter(
    brush
).transform_window(
    row_number='row_number()'
).transform_filter(
    alt.datum.row_number < 16
).add_params(
    d_select)

# site tables
site_text = alt.Chart(site_1141).mark_text(align='right', fontSize = 13).encode(
    y=alt.Y('row_number:O').axis(None),
    color=alt.condition(s_select, alt.value('#0a326a'), alt.value('black'))
).transform_filter(
    site_select
).transform_window(
    row_number='row_number()'
).transform_filter(
    alt.datum.row_number < 16
).add_params(
    site_select, s_select)

site_col = site_text.encode(text='SNE ID').properties(
    title=alt.Title(text='Location', align='right')
)
chas_col = site_text.encode(text='Chassis Category').properties(
    title=alt.Title(text='Chassis', align='right')
)
dev_col = site_text.encode(text='Device Model').properties(
    title=alt.Title(text='Device', align='right')
)
date_col = site_text.encode(text='date').properties(
    title=alt.Title(text='date', align='right')
)

site_table = alt.hconcat(site_col, chas_col, dev_col, date_col)

# # Data Tables
horsepower = ranked_text.encode(text='DND').properties(
    title=alt.Title(text='DND', align='right'))

mpg = ranked_text.encode(text='Location').properties(
    title=alt.Title(text='Location', align='right')
)

origin = ranked_text.encode(text='Chassis Category').properties(
    title=alt.Title(text='Category', align='right')
)

status = ranked_text.encode(text='status').properties(
    title=alt.Title(text='status', align='right')
)

# text = alt.hconcat(horsepower, mpg) # Combine data tables

quarter = alt.Chart(grp_df).mark_rect().encode(
    alt.Y('DND:N').axis(orient='right').title(''),
    #x='Failover Capacity:O',
    color=alt.condition(click, alt.value('steelblue'), alt.value('grey'))
).add_params(
    click).transform_filter(
    brush
    )

dchart = Chart.add_params(
    d_select
).transform_filter(
    d_select  ###### replace d_select !!!!
)

text = alt.hconcat(horsepower, mpg, origin, status)

# # Build chart()
(alt.vconcat(points ,  text)| dchart).configure_view(
    stroke=None
).configure_axis(
    grid=False, 
    labelFontSize=13,
    titleFontSize = 14
)#.save("C:/Users/614532416/Documents/Capacity Management/Capacity Dashboard/Backhaul Performance/sample_traffic_chart.html") 


alt.HConcatChart(...)

In [74]:
grp_df.replace({'Strategic': 'Pr2', 'Pr1': '', 'Legacy': 'Pr3', 'delivery': 'UP', None: 'DOWN'}, inplace=True)

In [75]:
ite = grp_df['1141 Code'].unique()
for i in ite:
    grp_df.replace({i: str(abs(hash(i)))[:7]}, inplace=True)

In [76]:
ite = grp_df['SNE'].unique()
for i in ite:
    grp_df.replace({i: str(abs(hash(i)))[:7]}, inplace=True)

In [19]:
len(grp_df['1141 Code'].unique())

342

In [49]:
grp_df

SNE  Failover Capacity   max_diff     slope  intercept   threshold  \
0    3364807               20.0   3.712176 -0.003677  16.379771   25.008799   
1    8702222               20.0   6.188542  0.012418  10.063760  301.806331   
2    8577122               20.0   4.011126  0.014234  12.519533  243.733188   
3    1069256               20.0  12.613039  0.033636   1.593864  172.230102   
4    4207736               10.0   3.864181  0.034072   3.096562   89.201006   
..       ...                ...        ...       ...        ...         ...   
344  7638433               10.0   3.764659  0.032275   1.565017  144.703686   
345  1291621               10.0   7.134742  0.075220  -6.560868  125.313704   
346  4750804               20.0   4.946541  0.028583   9.543349  192.775171   
347  2788301               10.0   3.927837  0.024222   3.851643   91.672624   
348  3359248               20.0   6.100658  0.034942   7.970032  169.692253   

    1141 Code   SNE ID Chassis Category Device Model     date status  
0     3757039  3364807              Pr2   7750 SR-12  2023-Q1     UP  
1     4306541  8702222              Pr3   7750 SR-12  2028-Q2   DOWN  
2     8455683  8577122              Pr2   7750 SR-12  2027-Q2   DOWN  
3     6301761  1069256              Pr3   7750 SR-12  2025-Q4     UP  
4     2071895  4207736              Pr2   7750 SR-12  2024-Q2   DOWN  
..        ...      ...              ...          ...      ...    ...  
344   5203408  7638433              Pr2   7750 SR-12  2025-Q2   DOWN  
345   5223037  1291621              Pr2   7750 SR-12  2025-Q1   DOWN  
346   4529616  4750804              Pr2   7750 SR-12  2026-Q2   DOWN  
347   6098216  2788301              Pr2   7750 SR-12  2024-Q2   DOWN  
348   2272334  3359248              Pr2   7750 SR-12  2025-Q4   DOWN  

[349 rows x 12 columns]

In [33]:
str(hash('ACWo'))[:8]

'31241943'

In [79]:
data[['Failover Capacity', 'Max Rx Tx', 'Total Capacity', 'trend_val']] = data[['Failover Capacity', 'Max Rx Tx', 'Total Capacity', 'trend_val']]/5

In [64]:
data

SNE  Max Rx Tx       date  Failover Capacity  Total Capacity  \
0       3328444   0.505002 2023-11-05                2.0             4.0   
1       3328444   0.473073 2023-10-29                2.0             4.0   
2       3328444   0.459666 2023-10-22                2.0             4.0   
3       3328444   0.471433 2023-10-15                2.0             4.0   
4       3328444   0.475933 2023-10-08                2.0             4.0   
...         ...        ...        ...                ...             ...   
225473  3453046        NaN 2024-07-21                4.0             8.0   
225474  3453046        NaN 2024-07-28                4.0             8.0   
225475  3453046        NaN 2024-08-04                4.0             8.0   
225476  3453046        NaN 2024-08-11                4.0             8.0   
225477  3453046        NaN 2024-08-18                4.0             8.0   

        trend_val 1141 Code  
0        0.521603       LTK  
1        0.521998       LTK  
2        0.522393       LTK  
3        0.522787       LTK  
4        0.523182       LTK  
...           ...       ...  
225473   1.032509       AGV  
225474   1.023367       AGV  
225475   1.014224       AGV  
225476   1.005082       AGV  
225477   0.995939       AGV  

[225478 rows x 7 columns]

In [77]:
ite = site_1141['SNE ID'].unique()
for i in ite:
    site_1141.replace({i: str(abs(hash(i)))[:7]}, inplace=True)

In [78]:
ite = data['SNE'].unique()
for i in ite:
    data.replace({i: str(abs(hash(i)))[:7]}, inplace=True)

In [93]:
data = data[data['DND'].isin(grp_df['DND'].unique())]

In [94]:
data.shape

(35249, 7)